In [5]:
from model.LongTermAccompanimentBeatwise import LongTermAccompanimentBeatwise
from model import load_model
import torch
from hvo_sequence.hvo_seq import HVO_Sequence
from hvo_sequence.drum_mappings import ROLAND_REDUCED_MAPPING
from bokeh.plotting import show, output_notebook
import os 

output_notebook()

mdl_ = 'misc/LTA/smooth-river-5_1plyjscj/000.pth'
model = load_model(
    model_path=mdl_,
    model_class=LongTermAccompanimentBeatwise,
    device='cpu',
    is_evaluating=True
)
model.serialize(save_folder=os.path.dirname(mdl_), filename=mdl_.split('/')[-1].replace('.pth', '.pt'))
model.eval()


Loading BokehJS ...

/home/dtic/miniconda3/envs/GrooveTransformer/lib/python3.9/site-packages/torch/jit/_recursive.py:266: UserWarning: 'batch_first' was found in ScriptModule constants, but was not actually set in __init__. Consider removing it.
  warnings.warn("'{}' was found in ScriptModule constants, "
/home/dtic/miniconda3/envs/GrooveTransformer/lib/python3.9/site-packages/torch/jit/_recursive.py:260: UserWarning: 'norm' was found in ScriptModule constants,  but it is a non-constant submodule. Consider removing it.
  warnings.warn("'{}' was found in ScriptModule constants, "


LongTermAccompanimentBeatwise(
  (SegmentEncoder): SegmentEncoder(
    (InputLayerEncoder): InputGrooveRhythmLayer(
      (velocity_dropout): Dropout(p=0.1, inplace=False)
      (offset_dropout): Dropout(p=0.1, inplace=False)
      (HitsLinear): Linear(in_features=1, out_features=128, bias=True)
      (VelocitiesLinear): Linear(in_features=1, out_features=128, bias=True)
      (OffsetsLinear): Linear(in_features=1, out_features=128, bias=True)
      (HitsReLU): ReLU()
      (VelocitiesReLU): ReLU()
      (OffsetsReLU): ReLU()
      (PositionalEncoding): PositionalEncoding(
        (dropout): Dropout(p=0.1, inplace=False)
      )
    )
    (Encoder): TransformerEncoder(
      (Encoder): TransformerEncoder(
        (layers): ModuleList(
          (0-3): 4 x TransformerEncoderLayer(
            (self_attn): MultiheadAttention(
              (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
            )
            (linear1): Linear(in_features=128,

In [6]:
# load data

from data import PairedLTADatasetV2
max_n_bars = 32

test_dataset = PairedLTADatasetV2(
        input_inst_dataset_bz2_filepath="data/lmd/data_bass_groove_test.bz2",
        output_inst_dataset_bz2_filepath="data/lmd/data_drums_full_unsplit.bz2",
        shift_tgt_by_n_steps=16,
        max_input_bars=max_n_bars,
        hop_n_bars=8,
        input_has_velocity=True,
        input_has_offsets=True
    )

INFO:data.Base.dataLoaders:PairedLTADatasetV2 Constructor --> Loading Cached Version from: cached/TorchDatasets/PairedLTADatasetV2_data_bass_groove_test.bz2_data_drums_full_unsplit.bz2_32_8_True_True_16.bz2pickle


In [7]:
def batch_data_extractor(data_, device='cpu'):

    bass_solo = data_[0].to(device) if data_[0].device.type != device else data_[0]
    drums = data_[1].to(device) if data_[1].device.type != device else data_[1]
    stacked_bass_drums = data_[2].to(device) if data_[2].device.type != device else data_[2]
    shifted_drums = data_[3].to(device) if data_[3].device.type != device else data_[3]

    return bass_solo, drums, stacked_bass_drums, shifted_drums


def predict_using_batch_data(batch_data, num_input_bars=None, model_=model, device='cpu'):
    model_.eval()



    bass_solo, drums, stacked_bass_drums, shifted_drums = batch_data_extractor(
        data_=batch_data,
        device=device
    )

    

    with torch.no_grad():
        h, v, o, hvo = model_.sample(
            src=bass_solo,
            tgt=shifted_drums
        )
    return hvo

In [27]:
import numpy as np
import timeit
sample_ix = np.random.randint(0, len(test_dataset))
print(sample_ix)

# select a random sample


hvo = predict_using_batch_data(test_dataset[sample_ix:sample_ix+1], model_=model, num_input_bars=torch.tensor([32]))

hvo_gt = test_dataset.instrument2_hvos[sample_ix][-64:, :]



total = torch.cat([hvo_gt, hvo[0]], dim=0)


hvo_seq = HVO_Sequence(
    beat_division_factors=[4],
    drum_mapping=ROLAND_REDUCED_MAPPING
)
hvo_seq.add_tempo(0, 120)
hvo_seq.add_time_signature(0, 4, 4)
print(total.cpu().numpy().shape)
hvo_seq.hvo = total.cpu().numpy()
hvo_seq.to_html_plot(show_figure=True, width=1400, height=400)



2048
(576, 27)


Figure(id='10010', ...)

In [28]:
hvo_seq2 = HVO_Sequence(
    beat_division_factors=[4], 
    drum_mapping=ROLAND_REDUCED_MAPPING
)
hvo_seq2.add_tempo(0, 120)
hvo_seq2.add_time_signature(0, 4, 4)
hvo_seq2.hvo = torch.cat([hvo_gt[:32, :], hvo[0]], dim=0).cpu().numpy()

# load audio player
from IPython.display import Audio
Audio(hvo_seq2.synthesize(sf_path='hvo_sequence/soundfonts/Standard_Drum_Kit.sf2'), rate=44100)


fluidsynth: error: Unknown integer parameter 'synth.sample-rate'


In [ ]:

# Auto-regressive prediction
def predict_using_batch_data_auto_Reg(batch_data, num_input_bars=None, model_=model, device='cpu'):
    model_.eval()

    in_len = 32 * 16
    out_len = 32
    in_step_start = 0
    in_n_steps = in_len
    out_step_start = in_len
    out_n_steps = out_len

    bass_solo, drums, stacked_bass_drums, shifted_drums = batch_data_extractor(
        data_=batch_data,
        device=device
    )

    enc_src = bass_solo 
    dec_src = shifted_drums 
    print(shifted_output.shape)
    if num_input_bars is None:
        num_input_bars = torch.ones((enc_src.shape[0], 1), dtype=torch.long).to(device) * 32

    hvo_in = torch.zeros((1, 32, 27))

    start = timeit.default_timer()


    for i in range(32):
        
        with torch.no_grad():
            
            h, v, o, hvo_ = model_.sample(
                src=enc_src,
                src_key_padding_and_memory_mask=create_src_mask(num_input_bars, 32).to(device),
                tgt=hvo_in,
                scale_vel=1.2
            )
            
        if i < 31:
            hvo_in[:, i+1, :] = hvo_[:, i, :]
    
    print('Time: ', (timeit.default_timer() - start) * 1000, 'ms')
        
    return hvo_

In [ ]:
import numpy as np
import timeit



# select a random sample
sample_ix = np.random.randint(0, len(test_dataset))
print(sample_ix)
hvo = predict_using_batch_data_auto_Reg(test_dataset[sample_ix:sample_ix+1], model_=model, num_input_bars=torch.tensor([32]))

hvo_gt = test_dataset.instrument2_hvos[sample_ix][-64:, :]



total = torch.cat([hvo_gt, hvo[0]], dim=0)


hvo_seq = HVO_Sequence(
    beat_division_factors=[4],
    drum_mapping=ROLAND_REDUCED_MAPPING
)
hvo_seq.add_tempo(0, 120)
hvo_seq.add_time_signature(0, 4, 4)
print(total.cpu().numpy().shape)
hvo_seq.hvo = total.cpu().numpy()
hvo_seq.to_html_plot(show_figure=True, width=800, height=400)



In [ ]:
hvo_seq2 = HVO_Sequence(
    beat_division_factors=[4], 
    drum_mapping=ROLAND_REDUCED_MAPPING
)

hvo_seq2.add_tempo(0, 120)
hvo_seq2.add_time_signature(0, 4, 4)
hvo_seq2.hvo = torch.cat([hvo_gt[:32, :], hvo[0]], dim=0).cpu().numpy()

# load audio player
from IPython.display import Audio
Audio(hvo_seq2.synthesize(sf_path='hvo_sequence/soundfonts/Standard_Drum_Kit.sf2'), rate=44100)


In [ ]:
# mdl_ = 'misc/LTA/charmed-disco-56_jwwbslj7/160.pth'
# model = load_model(
#     model_path=mdl_,
#     model_class=LongTermAccompanimentHierarchical,
#     device='cpu',
#     is_evaluating=True
# )
# model.eval()

model.reset()
sample_ix = np.random.randint(0, len(test_dataset))
print(sample_ix)
i1, i2, i12 = test_dataset[sample_ix:sample_ix+1]

i1_rand = i1[:, :32*32, :].clone() * 0
i2_rand = i2[:, :32*32, :]
hvo_gt = test_dataset.instrument2_hvos[sample_ix][-64:, :]

model.encode_varying_length_performance(i1_rand, i2_rand)
print(model.num_bars_encoded_so_far)

h, v, o, hvo = model.get_next_2_bars(0.5)
total = torch.cat([hvo_gt[:32, :], hvo[0]], dim=0)

from hvo_sequence.hvo_seq import HVO_Sequence
from hvo_sequence.drum_mappings import ROLAND_REDUCED_MAPPING
hvo_seq2 = HVO_Sequence(
    beat_division_factors=[4],
    drum_mapping=ROLAND_REDUCED_MAPPING
)
hvo_seq2.add_tempo(0, 120)
hvo_seq2.add_time_signature(0, 4, 4)
hvo_seq2.hvo = total.cpu().numpy()

hvo_seq2.to_html_plot(show_figure=True, width=800, height=400)

In [ ]:
2aq # load audio player
from IPython.display import Audio

Audio(hvo_seq2.synthesize(sf_path='hvo_sequence/soundfonts/Standard_Drum_Kit.sf2'), rate=44100)